### function to calculate minimum probility p_min to check given condition

In [1]:
def p_minimum(n,trail_cap,B_cap,B_bar):
        p_min = 1.0;
        for i in range(0,n):
            p_min *= trail_cap[i].wt
        p_min = p_min * B_cap[nrounds - 1 - (n + 1)]; 
        p_min = B_bar/p_min
        #print(B_bar,p_min)
        return p_min

### function to check given inputs are available in highways path list or not 

In [2]:
def highwaylist():
    alph,bet,gam,pro = [],[],[],[]
    with open('alph.txt') as ip1, open('bet.txt') as ip2, open('gam.txt') as ip3, open('pro.txt') as ip4:
        for i1,i2,i3,i4 in zip(ip1,ip2,ip3,ip4):
            hw.append(NMTS(int(i1.strip()),int(i2.strip()),int(i3.strip()),float(i4.strip()))) 
            

### function to calculate weight 

In [3]:
def weight(alpha1,beta1,gamma1): 
    if(alpha1==0 and beta1==0 and gamma1==0):
        return -200
    x1= (alpha1 << 1)& mask
    y1= (beta1  << 1)& mask
    z1= (gamma1  << 1)& mask
    not_x=(x1^mask)
    eq=((not_x)^y1)&(not_x^z1)
    s=eq&(alpha1^beta1^gamma1^(y1))
    if(s==0):        
        h=bin((~eq)& mask)
        wt=(h[1:].count("1"))
        return math.pow(2,-wt)
    else:
        return -200

In [4]:
#weight(0, 673, 0)

In [5]:
##function to update croad with prob more than pmin and output is in highway

In [6]:
def PDDT1(n,p_thres,k,wt,da,db,dc,s,maxddt,ddt):
    if(n==k):
        ddt.append(NMTS(da,db,dc,wt))
        #print(da,db,dc,s)
        if(wt>=s):
            maxddt.append(NMTS(da,db,dc,wt))
            #print(maxddt[0].dx,maxddt[0].dy,maxddt[0].dz,maxddt[0].wt,s)
        #print(da,db,dc,wt)
        return 
    
    for z in range(0,2):
        new_dc= (dc | (z<<k) & mask)
        wt= weight(da,db,new_dc)
        if(wt >= p_thres or (k+1)!=n):                    
            PDDT1(n,p_thres,k+1,wt,da,db,new_dc,s,maxddt,ddt) 
            
    if(len(ddt)==0):
        return 0,ddt,maxddt
    else:
        return 1,ddt,maxddt
   

In [7]:
##fucntion to find output for which weight is max

In [8]:
def PDDT(n,p_thres,k,wt,da,db,dc,s,maxddt,ddt):
    if(n==k):
        ddt.append(NMTS(da,db,dc,wt))
        #print(da,db,dc,s)
        if(wt>=s):
            s=wt
            maxddt.append(NMTS(da,db,dc,s))
            #print(maxddt[0].dx,maxddt[0].dy,maxddt[0].dz,maxddt[0].wt,s)
        #print(da,db,dc,wt)
        return 
    
    for z in range(0,2):
        new_dc= (dc | (z<<k) & mask)
        wt= weight(da,db,new_dc)
        if(wt >= p_thres or (k+1)!=n):                    
            PDDT(n,p_thres,k+1,wt,da,db,new_dc,s,maxddt,ddt) 
            
    if(len(ddt)==0):
        return 0,ddt,maxddt
    else:
        return 1,ddt,maxddt
   

In [9]:
#ck,ddt,maxddt=PDDT(16,0.1,0,1,256,33802,0,s)
#print(ck)

### function to perform left and right circular rotation 

In [10]:

#right circular shifts
def ROR(x,r):
    x = ((x << (SPECK_TYPE - r)) + (x >> r)) & mask
    return x

#left circular shifts
def ROL(x,r):
    x = ((x >> (SPECK_TYPE - r)) + (x << r)) & mask
    return x

### main function for threshold search

In [ ]:
def threshold_search(n,nrounds,hw,B_cap,B_bar,B_barlist,st0,st1,op,w1):
    if(n == 0): 
        #print(n)
        #print("loop")
        #print(st1,st0,op,w1)
        B_cap_temp[nrounds-1]=w1*B_cap[nrounds-1-(n+1)]
        if(B_cap_temp[nrounds-1]>B_bar):
            B_barlist[n]=w1
            trail_cap[n]= NMTS(ROL(st1,alpha),st0,op,w1)
            st1=op
            st0=ROL(st0,beta)^st1
            return threshold_search(n+1,nrounds,hw,B_cap,B_bar,B_barlist,st0,st1,op,w1)
        else:
            return B_bar,B_cap 
            
    if((n > 0) & (n != (nrounds - 1))):
        #print(n)
        st1=ROR(st1,alpha)
        p_min=p_minimum(n,trail_cap,B_cap,B_bar)
        croad=[]
        #function that check output is in highway and weight is greater than p_min or not, if it is update croad
        maxddt,ddt,max_p=[],[],0
        ck,ddt,maxddt=PDDT1(SPECK_TYPE,0.1,0,1,st1,st0,0,p_min,maxddt,ddt)
        if(ck==1):
            for i in range(0,len(maxddt)):
                croad.append(NMTS(maxddt[i].dx,maxddt[i].dy,maxddt[i].dz,maxddt[i].wt))
                         
        #opcheck_in_highways(0,p_min,st1,st0)
        #if croad is still empty then fill it with max probility value for other outputs except highway
        if(len(croad) == 0):
            crddt,ddt,max_p=[],[],0
            #print(st1,st0,max_p)
            ck,ddt,crddt=PDDT(SPECK_TYPE,0,0,1,st1,st0,0,max_p,crddt,ddt)
            #max_p,output,ck=max(0,st1,st0)
            if(ck==1):
                for i in range(0,len(crddt)):
                    croad.append(NMTS(crddt[i].dx,crddt[i].dy,crddt[i].dz,crddt[i].wt))
            else:
                return B_bar,B_cap
        
        #for i in range(0,len(croad)):
            #print(croad[i].dx,croad[i].dy,croad[i].dz,croad[i].wt)
        #check the inputs in highway or not 
        crhw = []
        temphw=[]
        maxddt,ddt,max_p=[],[],0
        ck,ddt,maxddt=PDDT(SPECK_TYPE,0.1,0,1,st1,st0,0,max_p,maxddt,ddt)
        #val1,val2,val3,w,chk= searchinhighway(st1,st0)
        if(ck==1):
            for i in range(0,len(ddt)):
                crhw.append(NMTS(ddt[i].dx,ddt[i].dy,ddt[i].dz,ddt[i].wt))
        
        for i in range(0,len(croad)):
            crhw.append(NMTS(croad[i].dx,croad[i].dy,croad[i].dz,croad[i].wt))

            
        p_r=1
        for i in range(0,n):
            p_r *= trail_cap[i].wt
        for i in range(0,len(crhw)):
            B_cap_temp[nrounds-1]= p_r * crhw[i].wt * B_cap[nrounds - 1 - (n + 1)]
            if(B_cap_temp[nrounds-1]>B_bar):
                B_barlist[n]=p_r * crhw[i].wt
                trail_cap[n]=NMTS(ROL(crhw[i].dx,alpha),crhw[i].dy,crhw[i].dz,crhw[i].wt)
                st1=crhw[i].dz
                st0=ROL(st0,beta)^st1
                return threshold_search(n+1,nrounds,hw,B_cap,B_bar,B_barlist,st0,st1,op,w1)
            else:
                return B_bar,B_cap
            return B_bar,B_cap
                    
    if(n ==(nrounds - 1)):
        st1=ROR(st1,alpha)
        #print(n)
        crddt,ddt,max_p=[],[],0
        ck,ddt,crddt=PDDT(SPECK_TYPE,0.1,0,1,st1,st0,0,max_p,crddt,ddt)
        #max_p,output,ck=max(0,st1,st0)
        if(ck==1):
            p=crddt[0].wt
            op=crddt[0].dz
        else:
            crddt,ddt,max_p=[],[],0
            ck,ddt,crddt=PDDT(SPECK_TYPE,0,0,1,st1,st0,0,max_p,crddt,ddt)
            if(ck==1):
                p=crddt[0].wt
                op=crddt[0].dz
                if(p>=0.1):
                     hw.append(NMTS(st1,st0,op,p))
                
        if(ck==0):
            return B_bar,B_cap             
        p_r=1
        for i in range(0,n):
            p_r *= trail_cap[i].wt
        B_cap_temp[nrounds-1]=p * p_r
        if(B_cap_temp[nrounds-1]>B_bar):
            B_barlist[n]=B_cap_temp[nrounds-1]
            #print ("%.16f %.16f" % (B_cap_temp[n],B_bar))
            trail_cap[n]=NMTS(ROL(st1,alpha),st0,op,p)
            B_bar=B_cap_temp[nrounds-1]
            for i in range(0,len(B_cap)):
                B_cap[i]=B_barlist[i]
                B_bar=B_cap_temp[n]  
            for i in range(0,len(trail_cap)):
                print(trail_cap[i].dx,trail_cap[i].dy,trail_cap[i].dz,trail_cap[i].wt)
            return B_bar,B_cap
        else:
            return B_bar,B_cap
    

In [ ]:
import random
import math 
#alpha beta are for left and right circular shift     
alpha, beta = 8,3
#speck total number of round epresented by nrounds
nrounds,n,s=10,0,0
SPECK_TYPE=10
mask,wshift = 2 ** 32 - 1, 31
#B_cap=[0.00048,0.00048,0.0625,0.00048,0.00048,0.00048,0.00048,0.00048,0.00048]
B_cap,B_bar=[2**(-50),2**(-100),2**(-150),2**(-200),2**(-250),2**(-300),2**(-350),2**(-400),2**(-450)],2 ** (-450)
B_barlist=[0]*nrounds
#B_cap,B_bar=[2**(-11),2**(-22),2**(-33),2**(-38)],2 ** (-38)
trail_cap,trail_bar=[0]*nrounds, [0]*nrounds
croad,hw,B_cap_temp=[],[],[0]*nrounds
st0=0xA60
st1=0x4205
hlen=3951388
max_p,output=0,0
maxddt,ddt,max_p=[],[],0
print ("%.30f" % B_bar)
class NMTS(object):
    """__init__() functions as the class constructor"""
    def __init__(self, dx=None, dy=None, dz=None, wt=None):
        self.dx = dx
        self.dy = dy
        self.dz = dz
        self.wt = wt
        
highwaylist()
for ch in range(0,len(hw)):
    #print(n,nrounds,B_bar,hw[ch].dx,hw[ch].dy,hw[ch].dz,hw[ch].wt)
    B_bar,B_cap =threshold_search(n,nrounds,hw,B_cap,B_bar,B_barlist,hw[ch].dx,hw[ch].dy,hw[ch].dz,hw[ch].wt)
    #print("%.30f" %B_bar,ch)
    print(B_bar,ch)
    #for i in range(0,len(B_cap)):
        #print(B_cap[i])

0.000000000000000000000000000000
3.4395525670743494e-136 0
3.4395525670743494e-136 1
3.4395525670743494e-136 2
3.4395525670743494e-136 3
3.4395525670743494e-136 4
3.4395525670743494e-136 5
3.4395525670743494e-136 6
3.4395525670743494e-136 7
3.4395525670743494e-136 8
3.4395525670743494e-136 9
3.4395525670743494e-136 10
3.4395525670743494e-136 11
3.4395525670743494e-136 12
3.4395525670743494e-136 13
3.4395525670743494e-136 14
3.4395525670743494e-136 15
3.4395525670743494e-136 16
3.4395525670743494e-136 17
3.4395525670743494e-136 18
3.4395525670743494e-136 19
3.4395525670743494e-136 20
3.4395525670743494e-136 21
3.4395525670743494e-136 22
3.4395525670743494e-136 23
3.4395525670743494e-136 24
3.4395525670743494e-136 25
3.4395525670743494e-136 26
3.4395525670743494e-136 27
3.4395525670743494e-136 28
3.4395525670743494e-136 29
3.4395525670743494e-136 30
3.4395525670743494e-136 31
3.4395525670743494e-136 32
3.4395525670743494e-136 33
3.4395525670743494e-136 34
3.4395525670743494e-136 35
3.439

3.4395525670743494e-136 532
3.4395525670743494e-136 533
3.4395525670743494e-136 534
3.4395525670743494e-136 535
3.4395525670743494e-136 536
3.4395525670743494e-136 537
3.4395525670743494e-136 538
3.4395525670743494e-136 539
3.4395525670743494e-136 540
3.4395525670743494e-136 541
3.4395525670743494e-136 542
3.4395525670743494e-136 543
3.4395525670743494e-136 544
3.4395525670743494e-136 545
3.4395525670743494e-136 546
3.4395525670743494e-136 547
3.4395525670743494e-136 548
3.4395525670743494e-136 549
3.4395525670743494e-136 550
3.4395525670743494e-136 551
3.4395525670743494e-136 552
3.4395525670743494e-136 553
3.4395525670743494e-136 554
3.4395525670743494e-136 555
3.4395525670743494e-136 556
3.4395525670743494e-136 557
3.4395525670743494e-136 558
3.4395525670743494e-136 559
3.4395525670743494e-136 560
3.4395525670743494e-136 561
3.4395525670743494e-136 562
3.4395525670743494e-136 563
3.4395525670743494e-136 564
3.4395525670743494e-136 565
3.4395525670743494e-136 566
3.4395525670743494e-

3.4395525670743494e-136 1199
3.4395525670743494e-136 1200
3.4395525670743494e-136 1201
3.4395525670743494e-136 1202
3.4395525670743494e-136 1203
3.4395525670743494e-136 1204
3.4395525670743494e-136 1205
3.4395525670743494e-136 1206
3.4395525670743494e-136 1207
3.4395525670743494e-136 1208
3.4395525670743494e-136 1209
3.4395525670743494e-136 1210
3.4395525670743494e-136 1211
3.4395525670743494e-136 1212
3.4395525670743494e-136 1213
3.4395525670743494e-136 1214
3.4395525670743494e-136 1215
3.4395525670743494e-136 1216
3.4395525670743494e-136 1217
3.4395525670743494e-136 1218
3.4395525670743494e-136 1219
3.4395525670743494e-136 1220
3.4395525670743494e-136 1221
3.4395525670743494e-136 1222
3.4395525670743494e-136 1223
3.4395525670743494e-136 1224
3.4395525670743494e-136 1225
3.4395525670743494e-136 1226
3.4395525670743494e-136 1227
3.4395525670743494e-136 1228
3.4395525670743494e-136 1229
3.4395525670743494e-136 1230
3.4395525670743494e-136 1231
3.4395525670743494e-136 1232
3.439552567074

3.4395525670743494e-136 2000
3.4395525670743494e-136 2001
3.4395525670743494e-136 2002
3.4395525670743494e-136 2003
3.4395525670743494e-136 2004
3.4395525670743494e-136 2005
3.4395525670743494e-136 2006
3.4395525670743494e-136 2007
3.4395525670743494e-136 2008
3.4395525670743494e-136 2009
3.4395525670743494e-136 2010
3.4395525670743494e-136 2011
3.4395525670743494e-136 2012
3.4395525670743494e-136 2013
3.4395525670743494e-136 2014
3.4395525670743494e-136 2015
3.4395525670743494e-136 2016
3.4395525670743494e-136 2017
3.4395525670743494e-136 2018
3.4395525670743494e-136 2019
3.4395525670743494e-136 2020
3.4395525670743494e-136 2021
3.4395525670743494e-136 2022
3.4395525670743494e-136 2023
3.4395525670743494e-136 2024
3.4395525670743494e-136 2025
3.4395525670743494e-136 2026
3.4395525670743494e-136 2027
3.4395525670743494e-136 2028
3.4395525670743494e-136 2029
3.4395525670743494e-136 2030
3.4395525670743494e-136 2031
3.4395525670743494e-136 2032
3.4395525670743494e-136 2033
3.439552567074

3.4395525670743494e-136 2770
3.4395525670743494e-136 2771
3.4395525670743494e-136 2772
3.4395525670743494e-136 2773
3.4395525670743494e-136 2774
3.4395525670743494e-136 2775
3.4395525670743494e-136 2776
3.4395525670743494e-136 2777
3.4395525670743494e-136 2778
3.4395525670743494e-136 2779
3.4395525670743494e-136 2780
3.4395525670743494e-136 2781
3.4395525670743494e-136 2782
3.4395525670743494e-136 2783
3.4395525670743494e-136 2784
3.4395525670743494e-136 2785
3.4395525670743494e-136 2786
3.4395525670743494e-136 2787
3.4395525670743494e-136 2788
3.4395525670743494e-136 2789
3.4395525670743494e-136 2790
3.4395525670743494e-136 2791
3.4395525670743494e-136 2792
3.4395525670743494e-136 2793
3.4395525670743494e-136 2794
3.4395525670743494e-136 2795
3.4395525670743494e-136 2796
3.4395525670743494e-136 2797
3.4395525670743494e-136 2798
3.4395525670743494e-136 2799
3.4395525670743494e-136 2800
3.4395525670743494e-136 2801
3.4395525670743494e-136 2802
3.4395525670743494e-136 2803
3.439552567074

...

3.4395525670743494e-136 152995
3.4395525670743494e-136 152996
3.4395525670743494e-136 152997
3.4395525670743494e-136 152998
3.4395525670743494e-136 152999
3.4395525670743494e-136 153000
3.4395525670743494e-136 153001
3.4395525670743494e-136 153002
3.4395525670743494e-136 153003
3.4395525670743494e-136 153004
3.4395525670743494e-136 153005
3.4395525670743494e-136 153006
3.4395525670743494e-136 153007
3.4395525670743494e-136 153008
3.4395525670743494e-136 153009
3.4395525670743494e-136 153010
3.4395525670743494e-136 153011
3.4395525670743494e-136 153012
3.4395525670743494e-136 153013
3.4395525670743494e-136 153014
3.4395525670743494e-136 153015
3.4395525670743494e-136 153016
3.4395525670743494e-136 153017
3.4395525670743494e-136 153018
3.4395525670743494e-136 153019
3.4395525670743494e-136 153020
3.4395525670743494e-136 153021
3.4395525670743494e-136 153022
3.4395525670743494e-136 153023
3.4395525670743494e-136 153024
3.4395525670743494e-136 153025
3.4395525670743494e-136 153026
3.439552

3.4395525670743494e-136 153721
3.4395525670743494e-136 153722
3.4395525670743494e-136 153723
3.4395525670743494e-136 153724
3.4395525670743494e-136 153725
3.4395525670743494e-136 153726
3.4395525670743494e-136 153727
3.4395525670743494e-136 153728
3.4395525670743494e-136 153729
3.4395525670743494e-136 153730
3.4395525670743494e-136 153731
3.4395525670743494e-136 153732
3.4395525670743494e-136 153733
3.4395525670743494e-136 153734
3.4395525670743494e-136 153735
3.4395525670743494e-136 153736
3.4395525670743494e-136 153737
3.4395525670743494e-136 153738
3.4395525670743494e-136 153739
3.4395525670743494e-136 153740
3.4395525670743494e-136 153741
3.4395525670743494e-136 153742
3.4395525670743494e-136 153743
3.4395525670743494e-136 153744
3.4395525670743494e-136 153745
3.4395525670743494e-136 153746
3.4395525670743494e-136 153747
3.4395525670743494e-136 153748
3.4395525670743494e-136 153749
3.4395525670743494e-136 153750
3.4395525670743494e-136 153751
3.4395525670743494e-136 153752
3.439552

3.4395525670743494e-136 154568
3.4395525670743494e-136 154569
3.4395525670743494e-136 154570
3.4395525670743494e-136 154571
3.4395525670743494e-136 154572
3.4395525670743494e-136 154573
3.4395525670743494e-136 154574
3.4395525670743494e-136 154575
3.4395525670743494e-136 154576
3.4395525670743494e-136 154577
3.4395525670743494e-136 154578
3.4395525670743494e-136 154579
3.4395525670743494e-136 154580
3.4395525670743494e-136 154581
3.4395525670743494e-136 154582
3.4395525670743494e-136 154583
3.4395525670743494e-136 154584
3.4395525670743494e-136 154585
3.4395525670743494e-136 154586
3.4395525670743494e-136 154587
3.4395525670743494e-136 154588
3.4395525670743494e-136 154589
3.4395525670743494e-136 154590
3.4395525670743494e-136 154591
3.4395525670743494e-136 154592
3.4395525670743494e-136 154593
3.4395525670743494e-136 154594
3.4395525670743494e-136 154595
3.4395525670743494e-136 154596
3.4395525670743494e-136 154597
3.4395525670743494e-136 154598
3.4395525670743494e-136 154599
3.439552

3.4395525670743494e-136 155444
3.4395525670743494e-136 155445
3.4395525670743494e-136 155446
3.4395525670743494e-136 155447
3.4395525670743494e-136 155448
3.4395525670743494e-136 155449
3.4395525670743494e-136 155450
3.4395525670743494e-136 155451
3.4395525670743494e-136 155452
3.4395525670743494e-136 155453
3.4395525670743494e-136 155454
3.4395525670743494e-136 155455
3.4395525670743494e-136 155456
3.4395525670743494e-136 155457
3.4395525670743494e-136 155458
3.4395525670743494e-136 155459
3.4395525670743494e-136 155460
3.4395525670743494e-136 155461
3.4395525670743494e-136 155462
3.4395525670743494e-136 155463
3.4395525670743494e-136 155464
3.4395525670743494e-136 155465
3.4395525670743494e-136 155466
3.4395525670743494e-136 155467
3.4395525670743494e-136 155468
3.4395525670743494e-136 155469
3.4395525670743494e-136 155470
3.4395525670743494e-136 155471
3.4395525670743494e-136 155472
3.4395525670743494e-136 155473
3.4395525670743494e-136 155474
3.4395525670743494e-136 155475
3.439552

3.4395525670743494e-136 156328
3.4395525670743494e-136 156329
3.4395525670743494e-136 156330
3.4395525670743494e-136 156331
3.4395525670743494e-136 156332
3.4395525670743494e-136 156333
3.4395525670743494e-136 156334
3.4395525670743494e-136 156335
3.4395525670743494e-136 156336
3.4395525670743494e-136 156337
3.4395525670743494e-136 156338
3.4395525670743494e-136 156339
3.4395525670743494e-136 156340
3.4395525670743494e-136 156341
3.4395525670743494e-136 156342
3.4395525670743494e-136 156343
3.4395525670743494e-136 156344
3.4395525670743494e-136 156345
3.4395525670743494e-136 156346
3.4395525670743494e-136 156347
3.4395525670743494e-136 156348
3.4395525670743494e-136 156349
3.4395525670743494e-136 156350
3.4395525670743494e-136 156351
3.4395525670743494e-136 156352
3.4395525670743494e-136 156353
3.4395525670743494e-136 156354
3.4395525670743494e-136 156355
3.4395525670743494e-136 156356
3.4395525670743494e-136 156357
3.4395525670743494e-136 156358
3.4395525670743494e-136 156359
3.439552